In [1]:
# https://github.com/Zackory/Keras-MNIST-GAN/blob/master/mnist_gan.py

import os
import numpy as np
import matplotlib.pyplot as plt

from keras.layers import Input
from keras.models import Model, Sequential
from keras.layers.core import Reshape, Dense, Dropout, Flatten
from keras.layers.advanced_activations import LeakyReLU
from keras.layers.convolutional import Convolution2D, UpSampling2D
from keras.layers.normalization import BatchNormalization
from keras.datasets import mnist
from keras.optimizers import Adam
from keras import initializers

# Deterministic output.
# Tired of seeing the same results every time? Remove the line below.
np.random.seed(1000)

# The results are a little better when the dimensionality of the random vector is only 10.
# The dimensionality has been left at 100 for consistency with other GAN implementations.
randomDim = 100

# Load MNIST data
(X_train, _), (_, _) = mnist.load_data()
X_train = (X_train.astype(np.float32) - 127.5)/127.5
X_train = X_train.reshape(60000, 784)

# Optimizer
adam = Adam(lr=0.0002, beta_1=0.5)

generator = Sequential()
generator.add(Dense(256, input_dim=randomDim, kernel_initializer=initializers.RandomNormal(stddev=0.02)))
generator.add(LeakyReLU(0.2))
generator.add(Dense(512))
generator.add(LeakyReLU(0.2))
generator.add(Dense(1024))
generator.add(LeakyReLU(0.2))
generator.add(Dense(784, activation='tanh'))
generator.compile(loss='binary_crossentropy', optimizer=adam)
print("---------------------------------- Generator Model Architecture --------------------------------------")
generator.summary()

discriminator = Sequential()
discriminator.add(Dense(1024, input_dim=784, kernel_initializer=initializers.RandomNormal(stddev=0.02)))
discriminator.add(LeakyReLU(0.2))
discriminator.add(Dropout(0.3))
discriminator.add(Dense(512))
discriminator.add(LeakyReLU(0.2))
discriminator.add(Dropout(0.3))
discriminator.add(Dense(256))
discriminator.add(LeakyReLU(0.2))
discriminator.add(Dropout(0.3))
discriminator.add(Dense(1, activation='sigmoid'))
discriminator.compile(loss='binary_crossentropy', optimizer=adam)
print("---------------------------------- Discriminator Model Architecture --------------------------------------")
discriminator.summary()

# Combined network
discriminator.trainable = False
# The generator takes noise as input and generates imgs
ganInput = Input(shape=(randomDim,))
x = generator(ganInput)
# The discriminator take generated images as input and determines validity
ganOutput = discriminator(x)
gan = Model(inputs=ganInput, outputs=ganOutput)
gan.compile(loss='binary_crossentropy', optimizer=adam)
print("---------------------------------- Combined Model/GAN Architecture  --------------------------------------")
gan.summary()


d_losses = []
g_losses = []

# Plot the loss from each batch
def plotLoss(epoch):
    plt.figure(figsize=(10, 8))
    plt.plot(dLosses, label='Discriminitive loss')
    plt.plot(gLosses, label='Generative loss')
    plt.xlabel('Epoch')
    plt.ylabel('Loss')
    plt.legend()
    plt.savefig('images/gan_loss_epoch_%d.png' % epoch)

# Create a wall of generated MNIST images
def plotGeneratedImages(epoch, examples=100, dim=(10, 10), figsize=(10, 10)):
    noise = np.random.normal(0, 1, size=[examples, randomDim])
    generatedImages = generator.predict(noise)
    generatedImages = generatedImages.reshape(examples, 28, 28)

    plt.figure(figsize=figsize)
    for i in range(generatedImages.shape[0]):
        plt.subplot(dim[0], dim[1], i+1)
        plt.imshow(generatedImages[i], interpolation='nearest', cmap='gray_r')
        plt.axis('off')
    plt.tight_layout()
    plt.savefig('images/gan_generated_image_epoch_%d.png' % epoch)

# Save the generator and discriminator networks (and weights) for later use
def saveModels(epoch):
    generator.save('models/gan_generator_epoch_%d.h5' % epoch)
    discriminator.save('models/gan_discriminator_epoch_%d.h5' % epoch)

def train(epochs=1, batch_size=128):
    batches = int(X_train.shape[0] / batch_size)

    for e in range(epochs):
        for batch_i in range(batches):
            
            # Get a random set of input noise and images
            real_images = X_train[np.random.randint(0, X_train.shape[0], size=batch_size)]

            # Generate fake MNIST images
            noise = np.random.normal(0, 1, size=[batch_size, randomDim])
            fake_images = generator.predict(noise)
            
            # print np.shape(real_images), np.shape(fake_images)
            X = np.concatenate([real_images, fake_images])

            # Labels for generated and real data
            y_dis = np.zeros(2*batch_size)
            # One-sided label smoothing
            y_dis[:batch_size] = 0.9

            # Train discriminator
            discriminator.trainable = True
            d_loss = discriminator.train_on_batch(X, y_dis)

            # Train generator
            noise = np.random.normal(0, 1, size=[batch_size, randomDim])
            yGen = np.ones(batch_size)
            discriminator.trainable = False
            g_loss = gan.train_on_batch(noise, yGen)
            
            cur_batch_progress = float(batch_i)/float(batches) * 100
            print("Epoch: {}/{}, current batch: {:.2f}%, d_loss: {:.5f}, g_loss: {:.5f}"
                  .format(e,epochs,cur_batch_progress,d_loss,g_loss))

        # Store loss of most recent batch from this epoch
        d_losses.append(d_loss)
        g_losses.append(g_loss)

        # if e % 20 == 0:
        # I want every epoch saving a png
        plotGeneratedImages(e)
        saveModels(e)

    # Plot losses from every epoch
    plotLoss(e)

train(200, 128)


Using TensorFlow backend.


---------------------------------- Generator Model Architecture --------------------------------------
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_1 (Dense)              (None, 256)               25856     
_________________________________________________________________
leaky_re_lu_1 (LeakyReLU)    (None, 256)               0         
_________________________________________________________________
dense_2 (Dense)              (None, 512)               131584    
_________________________________________________________________
leaky_re_lu_2 (LeakyReLU)    (None, 512)               0         
_________________________________________________________________
dense_3 (Dense)              (None, 1024)              525312    
_________________________________________________________________
leaky_re_lu_3 (LeakyReLU)    (None, 1024)              0         
_______________________________________

Epoch: 1/200, current progress: 12.61%, d_loss: 0.59681, g_loss: 1.04773
Epoch: 1/200, current progress: 12.82%, d_loss: 0.56128, g_loss: 0.81452
Epoch: 1/200, current progress: 13.03%, d_loss: 0.55991, g_loss: 1.13136
Epoch: 1/200, current progress: 13.25%, d_loss: 0.54379, g_loss: 0.85043
Epoch: 1/200, current progress: 13.46%, d_loss: 0.58014, g_loss: 1.12413
Epoch: 1/200, current progress: 13.68%, d_loss: 0.60709, g_loss: 0.62921
Epoch: 1/200, current progress: 13.89%, d_loss: 0.66391, g_loss: 0.86285
Epoch: 1/200, current progress: 14.10%, d_loss: 0.55257, g_loss: 0.98522
Epoch: 1/200, current progress: 14.32%, d_loss: 0.53320, g_loss: 0.87725
Epoch: 1/200, current progress: 14.53%, d_loss: 0.49971, g_loss: 1.14934
Epoch: 1/200, current progress: 14.74%, d_loss: 0.47096, g_loss: 1.08353
Epoch: 1/200, current progress: 14.96%, d_loss: 0.47562, g_loss: 1.47054
Epoch: 1/200, current progress: 15.17%, d_loss: 0.53287, g_loss: 0.58294
Epoch: 1/200, current progress: 15.38%, d_loss: 0.7

Epoch: 1/200, current progress: 36.97%, d_loss: 0.35517, g_loss: 2.10452
Epoch: 1/200, current progress: 37.18%, d_loss: 0.35052, g_loss: 2.00088
Epoch: 1/200, current progress: 37.39%, d_loss: 0.33982, g_loss: 2.31023
Epoch: 1/200, current progress: 37.61%, d_loss: 0.38877, g_loss: 0.98438
Epoch: 1/200, current progress: 37.82%, d_loss: 0.70981, g_loss: 3.15161
Epoch: 1/200, current progress: 38.03%, d_loss: 0.71889, g_loss: 0.78892
Epoch: 1/200, current progress: 38.25%, d_loss: 0.61432, g_loss: 1.03597
Epoch: 1/200, current progress: 38.46%, d_loss: 0.45151, g_loss: 1.95802
Epoch: 1/200, current progress: 38.68%, d_loss: 0.36806, g_loss: 1.91395
Epoch: 1/200, current progress: 38.89%, d_loss: 0.35186, g_loss: 1.64664
Epoch: 1/200, current progress: 39.10%, d_loss: 0.36180, g_loss: 2.00289
Epoch: 1/200, current progress: 39.32%, d_loss: 0.33558, g_loss: 1.96097
Epoch: 1/200, current progress: 39.53%, d_loss: 0.36143, g_loss: 1.79415
Epoch: 1/200, current progress: 39.74%, d_loss: 0.3

Epoch: 1/200, current progress: 61.32%, d_loss: 0.41091, g_loss: 1.97461
Epoch: 1/200, current progress: 61.54%, d_loss: 0.38472, g_loss: 2.60552
Epoch: 1/200, current progress: 61.75%, d_loss: 0.38354, g_loss: 1.74351
Epoch: 1/200, current progress: 61.97%, d_loss: 0.45754, g_loss: 2.90237
Epoch: 1/200, current progress: 62.18%, d_loss: 0.50937, g_loss: 0.86703
Epoch: 1/200, current progress: 62.39%, d_loss: 0.73262, g_loss: 2.73768
Epoch: 1/200, current progress: 62.61%, d_loss: 0.50859, g_loss: 1.64940
Epoch: 1/200, current progress: 62.82%, d_loss: 0.43223, g_loss: 2.15526
Epoch: 1/200, current progress: 63.03%, d_loss: 0.39703, g_loss: 2.18255
Epoch: 1/200, current progress: 63.25%, d_loss: 0.42095, g_loss: 1.74064
Epoch: 1/200, current progress: 63.46%, d_loss: 0.42173, g_loss: 3.02214
Epoch: 1/200, current progress: 63.68%, d_loss: 0.50470, g_loss: 0.62458
Epoch: 1/200, current progress: 63.89%, d_loss: 0.93671, g_loss: 3.26029
Epoch: 1/200, current progress: 64.10%, d_loss: 0.7

...

Epoch: 199/200, current progress: 82.91%, d_loss: 0.62670, g_loss: 1.12440
Epoch: 199/200, current progress: 83.12%, d_loss: 0.62451, g_loss: 1.32857
Epoch: 199/200, current progress: 83.33%, d_loss: 0.65119, g_loss: 0.89636
Epoch: 199/200, current progress: 83.55%, d_loss: 0.62345, g_loss: 0.98279
Epoch: 199/200, current progress: 83.76%, d_loss: 0.63093, g_loss: 1.12845
Epoch: 199/200, current progress: 83.97%, d_loss: 0.64449, g_loss: 1.09363
Epoch: 199/200, current progress: 84.19%, d_loss: 0.61268, g_loss: 1.07262
Epoch: 199/200, current progress: 84.40%, d_loss: 0.62133, g_loss: 1.07741
Epoch: 199/200, current progress: 84.62%, d_loss: 0.64912, g_loss: 1.03756
Epoch: 199/200, current progress: 84.83%, d_loss: 0.63809, g_loss: 1.08132
Epoch: 199/200, current progress: 85.04%, d_loss: 0.61306, g_loss: 1.07575
Epoch: 199/200, current progress: 85.26%, d_loss: 0.62620, g_loss: 0.97754
Epoch: 199/200, current progress: 85.47%, d_loss: 0.62078, g_loss: 1.01879
Epoch: 199/200, current p

Epoch: 200/200, current progress: 6.84%, d_loss: 0.64002, g_loss: 1.03963
Epoch: 200/200, current progress: 7.05%, d_loss: 0.63099, g_loss: 1.07652
Epoch: 200/200, current progress: 7.26%, d_loss: 0.63215, g_loss: 1.08306
Epoch: 200/200, current progress: 7.48%, d_loss: 0.67535, g_loss: 1.00165
Epoch: 200/200, current progress: 7.69%, d_loss: 0.61297, g_loss: 0.91221
Epoch: 200/200, current progress: 7.91%, d_loss: 0.63632, g_loss: 1.10188
Epoch: 200/200, current progress: 8.12%, d_loss: 0.63286, g_loss: 1.20926
Epoch: 200/200, current progress: 8.33%, d_loss: 0.60755, g_loss: 1.03689
Epoch: 200/200, current progress: 8.55%, d_loss: 0.61660, g_loss: 1.00807
Epoch: 200/200, current progress: 8.76%, d_loss: 0.60347, g_loss: 1.10312
Epoch: 200/200, current progress: 8.97%, d_loss: 0.59795, g_loss: 0.97043
Epoch: 200/200, current progress: 9.19%, d_loss: 0.62282, g_loss: 1.15605
Epoch: 200/200, current progress: 9.40%, d_loss: 0.58089, g_loss: 1.11836
Epoch: 200/200, current progress: 9.62

Epoch: 200/200, current progress: 30.56%, d_loss: 0.58704, g_loss: 0.98465
Epoch: 200/200, current progress: 30.77%, d_loss: 0.62960, g_loss: 1.00009
Epoch: 200/200, current progress: 30.98%, d_loss: 0.60381, g_loss: 1.11820
Epoch: 200/200, current progress: 31.20%, d_loss: 0.62430, g_loss: 1.00591
Epoch: 200/200, current progress: 31.41%, d_loss: 0.62847, g_loss: 1.11871
Epoch: 200/200, current progress: 31.62%, d_loss: 0.67448, g_loss: 1.11552
Epoch: 200/200, current progress: 31.84%, d_loss: 0.62502, g_loss: 1.08399
Epoch: 200/200, current progress: 32.05%, d_loss: 0.62081, g_loss: 1.03174
Epoch: 200/200, current progress: 32.26%, d_loss: 0.61727, g_loss: 1.01168
Epoch: 200/200, current progress: 32.48%, d_loss: 0.59989, g_loss: 1.03469
Epoch: 200/200, current progress: 32.69%, d_loss: 0.62405, g_loss: 1.06305
Epoch: 200/200, current progress: 32.91%, d_loss: 0.63369, g_loss: 1.04357
Epoch: 200/200, current progress: 33.12%, d_loss: 0.62305, g_loss: 1.17427
Epoch: 200/200, current p

Epoch: 200/200, current progress: 54.49%, d_loss: 0.59880, g_loss: 1.08118
Epoch: 200/200, current progress: 54.70%, d_loss: 0.62476, g_loss: 1.14793
Epoch: 200/200, current progress: 54.91%, d_loss: 0.63514, g_loss: 1.06423
Epoch: 200/200, current progress: 55.13%, d_loss: 0.60408, g_loss: 1.08187
Epoch: 200/200, current progress: 55.34%, d_loss: 0.61506, g_loss: 1.03498
Epoch: 200/200, current progress: 55.56%, d_loss: 0.66625, g_loss: 1.04384
Epoch: 200/200, current progress: 55.77%, d_loss: 0.64385, g_loss: 1.09525
Epoch: 200/200, current progress: 55.98%, d_loss: 0.63272, g_loss: 1.15948
Epoch: 200/200, current progress: 56.20%, d_loss: 0.64044, g_loss: 0.95172
Epoch: 200/200, current progress: 56.41%, d_loss: 0.62609, g_loss: 1.01082
Epoch: 200/200, current progress: 56.62%, d_loss: 0.61607, g_loss: 1.14661
Epoch: 200/200, current progress: 56.84%, d_loss: 0.63164, g_loss: 1.00782
Epoch: 200/200, current progress: 57.05%, d_loss: 0.61580, g_loss: 0.92850
Epoch: 200/200, current p

Epoch: 200/200, current progress: 78.42%, d_loss: 0.63608, g_loss: 1.00646
Epoch: 200/200, current progress: 78.63%, d_loss: 0.65513, g_loss: 0.97376
Epoch: 200/200, current progress: 78.85%, d_loss: 0.61393, g_loss: 0.99404
Epoch: 200/200, current progress: 79.06%, d_loss: 0.63106, g_loss: 1.13637
Epoch: 200/200, current progress: 79.27%, d_loss: 0.61795, g_loss: 1.12348
Epoch: 200/200, current progress: 79.49%, d_loss: 0.62185, g_loss: 1.02480
Epoch: 200/200, current progress: 79.70%, d_loss: 0.61928, g_loss: 1.20977
Epoch: 200/200, current progress: 79.91%, d_loss: 0.65365, g_loss: 0.97218
Epoch: 200/200, current progress: 80.13%, d_loss: 0.60162, g_loss: 1.06477
Epoch: 200/200, current progress: 80.34%, d_loss: 0.59966, g_loss: 1.02027
Epoch: 200/200, current progress: 80.56%, d_loss: 0.61565, g_loss: 0.97469
Epoch: 200/200, current progress: 80.77%, d_loss: 0.65391, g_loss: 1.06316
Epoch: 200/200, current progress: 80.98%, d_loss: 0.57937, g_loss: 1.19992
Epoch: 200/200, current p